# SmartCab

## Setup

In [1]:
# Colab
!rm -r smart-cities-drl
!git clone https://github.com/eescriba/smart-cities-drl
!cd smart-cities-drl/ && pip install -e .

import sys
sys.path.insert(0,'./smart-cities-drl/src/')

# Local
# !pip install -e ..
# import sys
# sys.path.insert(0,'../src/')

Cloning into 'smart-cities-drl'...
remote: Enumerating objects: 878, done.
remote: Counting objects: 100% (878/878), done.
remote: Compressing objects: 100% (616/616), done.
remote: Total 878 (delta 404), reused 678 (delta 225), pack-reused 0
Receiving objects: 100% (878/878), 10.81 MiB | 8.73 MiB/s, done.
Resolving deltas: 100% (404/404), done.
Obtaining file:///content/smart-cities-drl
  Found existing installation: smart-cities-drl 0.1.0
    Can't uninstall 'smart-cities-drl'. No files were found to uninstall.
  Running setup.py develop for smart-cities-drl


In [3]:
import json
import shutil
import random

import gym
import ray
from ray.tune import run, choice
from core.rl import PPOAgent
from core.pbt import PbtOptimizer
from smartcab.env import SmartCabEnv

/usr/local/lib/python3.7/dist-packages/ray/autoscaler/_private/cli_logger.py:61: FutureWarning: Not all Ray CLI dependencies were found. In Ray 1.4+, the Ray CLI, autoscaler, and dashboard will only be usable via `pip install 'ray[default]'`. Please update your install command.
  "update your install command.", FutureWarning)


Instructions for updating:
experimental_compile is deprecated, use jit_compile instead


## Proximal Policy Optimization (PPO)

### Tune hyperparameters

In [4]:
ppo = PPOAgent("smartcab_ppo_tune", SmartCabEnv, {})

2021-07-01 10:20:08,696	INFO services.py:1274 -- View the Ray dashboard at http://127.0.0.1:8265
2021-07-01 10:20:10,814	INFO trainer.py:671 -- Tip: set framework=tfe or the --eager flag to enable TensorFlow eager execution
2021-07-01 10:20:10,816	INFO trainer.py:698 -- Current log_level is WARN. For more information, set 'log_level': 'INFO' / 'DEBUG' or use the -v and -vv flags.
(pid=13954) WARNING:tensorflow:From /usr/local/lib/python3.7/dist-packages/tensorflow_probability/python/internal/variadic_reduce.py:115: calling function (from tensorflow.python.eager.def_function) with experimental_compile is deprecated and will be removed in a future version.
(pid=13954) Instructions for updating:
(pid=13954) experimental_compile is deprecated, use jit_compile instead
(pid=13955) WARNING:tensorflow:From /usr/local/lib/python3.7/dist-packages/tensorflow_probability/python/internal/variadic_reduce.py:115: calling function (from tensorflow.python.eager.def_function) with experimental_compile i

(pid=13954) [(1, 6), (2, 2), (5, 6), (6, 3)]
(pid=13954) Action Space:  Discrete(6)
(pid=13954) Observation Space:  Tuple(Box(0.0, 7.0, (2,), float32), Discrete(5), Discrete(4))
(pid=13955) [(1, 6), (2, 2), (5, 6), (6, 3)]
(pid=13955) Action Space:  Discrete(6)
(pid=13955) Observation Space:  Tuple(Box(0.0, 7.0, (2,), float32), Discrete(5), Discrete(4))


2021-07-01 10:20:21,732	INFO trainable.py:104 -- Trainable.setup took 10.920 seconds. If your trainable is slow to initialize, consider setting reuse_actors=True to reduce actor creation overheads.
2021-07-01 10:20:21,734	WARNING util.py:53 -- Install gputil for GPU system monitoring.


In [5]:
tune_config = {
    "env": SmartCabEnv,
    "seed": 123,
    "horizon": 100,
    "num_gpus": 1,
    "num_workers": 1,
    "observation_filter": "MeanStdFilter",
    "model": {
        "free_log_std": True
    },
    "lambda": 0.9,
    "clip_param": 0.3,
    "lr": 5e-5,
    "num_sgd_iter": choice([10, 20, 30]),
    "sgd_minibatch_size": choice([128, 256, 512]),
    "train_batch_size": choice([8000, 16000, 32000])
}
stop_criteria = {
    "timesteps_total": 1000000
}
hyperparam_mutations={
    "lambda": lambda: random.uniform(0.7, 1.0),
    "clip_param": lambda: random.uniform(0.1, 0.5),
    "lr": [1e-3, 5e-4, 1e-4, 5e-5, 1e-5],
    "num_sgd_iter": lambda: random.randint(1, 30),
    "sgd_minibatch_size": lambda: random.randint(128, 16384),
    "train_batch_size": lambda: random.randint(2000, 160000),
}
pbt = PbtOptimizer(hyperparam_mutations, metric="episode_reward_max", mode="max")

In [ ]:
ppo.restart()
analysis = ppo.tune(tune_config, stop_criteria, scheduler=pbt.scheduler)
best_config =  analysis.get_best_config(metric="episode_reward_mean", mode="max")
print("Best hyperparameters found: ", best_config)

2021-07-01 10:20:24,318	INFO services.py:1274 -- View the Ray dashboard at http://127.0.0.1:8265


(pid=14144) WARNING:tensorflow:From /usr/local/lib/python3.7/dist-packages/tensorflow_probability/python/internal/variadic_reduce.py:115: calling function (from tensorflow.python.eager.def_function) with experimental_compile is deprecated and will be removed in a future version.
(pid=14144) Instructions for updating:
(pid=14144) experimental_compile is deprecated, use jit_compile instead
(pid=14144) 2021-07-01 10:20:30,148	INFO trainer.py:671 -- Tip: set framework=tfe or the --eager flag to enable TensorFlow eager execution
(pid=14144) 2021-07-01 10:20:30,149	INFO trainer.py:698 -- Current log_level is WARN. For more information, set 'log_level': 'INFO' / 'DEBUG' or use the -v and -vv flags.


(pid=14145) WARNING:tensorflow:From /usr/local/lib/python3.7/dist-packages/tensorflow_probability/python/internal/variadic_reduce.py:115: calling function (from tensorflow.python.eager.def_function) with experimental_compile is deprecated and will be removed in a future version.
(pid=14145) Instructions for updating:
(pid=14145) experimental_compile is deprecated, use jit_compile instead


(pid=14145) [(1, 6), (2, 2), (5, 6), (6, 3)]
(pid=14145) Action Space:  Discrete(6)
(pid=14145) Observation Space:  Tuple(Box(0.0, 7.0, (2,), float32), Discrete(5), Discrete(4))


(pid=14145) WARNING:tensorflow:
(pid=14145) The following Variables were used a Lambda layer's call (lambda), but
(pid=14145) are not present in its tracked objects:
(pid=14145)   <tf.Variable 'default_policy/log_std:0' shape=(3,) dtype=float32>
(pid=14145) It is possible that this is intended behavior, but it is more likely
(pid=14145) an omission. This is a strong indication that this layer should be
(pid=14145) formulated as a subclassed Layer rather than a Lambda layer.
(pid=14144) WARNING:tensorflow:
(pid=14144) The following Variables were used a Lambda layer's call (lambda), but
(pid=14144) are not present in its tracked objects:
(pid=14144)   <tf.Variable 'default_policy/log_std:0' shape=(3,) dtype=float32>
(pid=14144) It is possible that this is intended behavior, but it is more likely
(pid=14144) an omission. This is a strong indication that this layer should be
(pid=14144) formulated as a subclassed Layer rather than a Lambda layer.
(pid=14144) 2021-07-01 10:20:38,219	WARNIN

...

(pid=39983) [(1, 6), (2, 2), (5, 6), (6, 3)]
(pid=39983) Action Space:  Discrete(6)
(pid=39983) Observation Space:  Tuple(Box(0.0, 7.0, (2,), float32), Discrete(5), Discrete(4))


(pid=39983) WARNING:tensorflow:
(pid=39983) The following Variables were used a Lambda layer's call (lambda), but
(pid=39983) are not present in its tracked objects:
(pid=39983)   <tf.Variable 'default_policy/log_std:0' shape=(3,) dtype=float32>
(pid=39983) It is possible that this is intended behavior, but it is more likely
(pid=39983) an omission. This is a strong indication that this layer should be
(pid=39983) formulated as a subclassed Layer rather than a Lambda layer.
(pid=39982) WARNING:tensorflow:
(pid=39982) The following Variables were used a Lambda layer's call (lambda), but
(pid=39982) are not present in its tracked objects:
(pid=39982)   <tf.Variable 'default_policy/log_std:0' shape=(3,) dtype=float32>
(pid=39982) It is possible that this is intended behavior, but it is more likely
(pid=39982) an omission. This is a strong indication that this layer should be
(pid=39982) formulated as a subclassed Layer rather than a Lambda layer.
(pid=39982) 2021-07-01 15:19:33,893	WARNIN

(pid=40102) [(1, 6), (2, 2), (5, 6), (6, 3)]
(pid=40102) Action Space:  Discrete(6)
(pid=40102) Observation Space:  Tuple(Box(0.0, 7.0, (2,), float32), Discrete(5), Discrete(4))


(pid=40102) WARNING:tensorflow:
(pid=40102) The following Variables were used a Lambda layer's call (lambda), but
(pid=40102) are not present in its tracked objects:
(pid=40102)   <tf.Variable 'default_policy/log_std:0' shape=(3,) dtype=float32>
(pid=40102) It is possible that this is intended behavior, but it is more likely
(pid=40102) an omission. This is a strong indication that this layer should be
(pid=40102) formulated as a subclassed Layer rather than a Lambda layer.
(pid=40075) WARNING:tensorflow:
(pid=40075) The following Variables were used a Lambda layer's call (lambda), but
(pid=40075) are not present in its tracked objects:
(pid=40075)   <tf.Variable 'default_policy/log_std:0' shape=(3,) dtype=float32>
(pid=40075) It is possible that this is intended behavior, but it is more likely
(pid=40075) an omission. This is a strong indication that this layer should be
(pid=40075) formulated as a subclassed Layer rather than a Lambda layer.
(pid=40075) 2021-07-01 15:19:49,582	INFO t

Result for PPO_SmartCabEnv_f4111_00001:
  agent_timesteps_total: 735352
  custom_metrics: {}
  date: 2021-07-01_15-20-10
  done: false
  episode_len_mean: 100.0
  episode_media: {}
  episode_reward_max: -69.0
  episode_reward_mean: -113.05128205128206
  episode_reward_min: -339.0
  episodes_this_iter: 78
  episodes_total: 7347
  experiment_id: c4f4e70b4d7944a692cc025e1c7c55db
  hostname: 8dbda79fea12
  info:
    learner:
      default_policy:
        learner_stats:
          cur_kl_coeff: 0.20000000298023224
          cur_lr: 9.999999747378752e-05
          entropy: 0.31464600563049316
          entropy_coeff: 0.0
          kl: 0.015871653333306313
          model: {}
          policy_loss: -0.015385804697871208
          total_loss: 46.72965621948242
          vf_explained_var: 0.6611731648445129
          vf_loss: 46.74186706542969
    num_agent_steps_sampled: 735352
    num_agent_steps_trained: 735352
    num_steps_sampled: 735352
    num_steps_trained: 735352
  iterations_since_res

In [ ]:
best_config = {
    "observation_filter": "MeanStdFilter",
    "model": {"free_log_std": True},
    "num_sgd_iter": 10,
    "sgd_minibatch_size": 128,
    "lambda": 0.731396,
    "clip_param": 0.317651,
    "lr": 5e-05,
    "train_batch_size": 18812,
}

### Training

In [ ]:
ppo = PPOAgent("smartcab_ppo_train", best_config, WasteNetEnv, {})
ppo.train(num_iter=200)

In [ ]:
policy = ppo.agent.get_policy()
model = policy.model
print(model.base_model.summary())

### Testing

In [ ]:
# ppo = PPOAgent("smartcab_ppo_test", best_config, SmartCabEnv, {})
# ppo.load("checkpoints/checkpoint-best")
ppo.test(num_episodes=1000)

### Visualization

In [ ]:
!zip -r /content/ray_results.zip /content/ray_results

In [ ]:
%load_ext tensorboard 
%tensorboard --logdir="/content/ray_results/"